# Scrape Pandas Table

In [197]:
from splinter import Browser
from bs4 import BeautifulSoup
import requests
import webbot as web
import pandas as pd
#import io

In [198]:
# Read in HTML tables into a DataFrame
browser = Browser('chrome')

In [199]:
# Select the second table
url = 'https://www.nassaucandy.com/customer/account/login/referer/aHR0cHM6Ly93d3cubmFzc2F1Y2FuZHkuY29tL2dyYWJhbmRnbw%2C%2C/'
browser.visit(url)

In [7]:
#user="Contact@buycarpediem.com"
#password="Kamilla2024"

In [212]:
#
url2='https://www.nassaucandy.com/1950-s-decade-box-9oz.html'
#url2='https://www.nassaucandy.com/gummybuildingblocks3dnassaucandy-n.html'
browser.visit(url2)

In [213]:

def scrape_product_data(url2):
    # Send HTTP request to the product URL
    product_response = requests.get(url2)
    product_soup = BeautifulSoup(product_response.content, 'html.parser')
    
    # Extract and return data from the product page
    product_title = None
    product_SKU = None
    products_information = None
    sales_per_case_element= None
    
    # Extract product title
    product_title_element = product_soup.find('h1')
    if product_title_element:
        product_title = product_title_element.text.strip()
    
    # Extract product SKU
    product_info_stock_sku_div = product_soup.find('div', class_='product-info-stock-sku')
    if product_info_stock_sku_div:
        product_SKU = product_info_stock_sku_div.text.strip()
    
    # Extract products information
    products_info_detailed_div = product_soup.find('div', class_='product data items')
    if products_info_detailed_div:
        products_information = products_info_detailed_div.text.strip()
    
    # Extract sales per case and quantity
    product_pack_info= product_soup.find('div', class_='qty-case')
    if product_pack_info:    
        sales_per_case_element = product_pack_info.text.strip()

    print("Title:", product_title) 
    print("SKU:", product_SKU)
    print('Products information:', products_information)  
    print("Sales Per Case:", sales_per_case_element)
    #print("Quantity:", qty)
    
    return product_title, product_SKU, products_information, sales_per_case_element

   

In [214]:
product_data=scrape_product_data(url2)
print(product_data)



Title: 1950'S DECADE BOX 9 OZ
SKU: SKU
52155
Products information: More Information                    




More Information


Kosher
No


Brand
NANCY ADAMS


UPC
618645521554


GTIN (case)
10618645521551


Country of Manufacture
United States


Pallet Pattern
12 cases per layer, 7 layers. 84 total cases per pallet.
Sales Per Case: None
("1950'S DECADE BOX 9 OZ", 'SKU\n52155', 'More Information                    \n\n\n\n\nMore Information\n\n\nKosher\nNo\n\n\nBrand\nNANCY ADAMS\n\n\nUPC\n618645521554\n\n\nGTIN (case)\n10618645521551\n\n\nCountry of Manufacture\nUnited States\n\n\nPallet Pattern\n12 cases per layer, 7 layers. 84 total cases per pallet.', None)


In [126]:
# Function to scrape data from multiple pages


def scrape_multiple_pages():
    page_number = 1
    all_product_data = []  # List to accumulate scraped data
    while True:
        # Send HTTP request to the current page URL
        page_response = requests.get(f'https://www.nassaucandy.com/confections.html?p={page_number}')
        page_soup = BeautifulSoup(page_response.content, 'html.parser')
        
         # Extract data from the current page
        product_links = []
        for div in page_soup.find_all('div', class_='product-item-info'):
            a_tag = div.find('a', href=True)
            if a_tag:
                product_links.append(a_tag['href'])

        for product_link in product_links:
            product_data = scrape_product_data(product_link)
            all_product_data.append(product_data)
        
        # Break if there's no next product to scrape
        if not product_links:
            break
        
        # Update page_number for the next iteration
        page_number += 1
    
    return all_product_data


In [127]:
product_list=scrape_multiple_pages()

for product_data in product_list:
    print(product_data)

Title: 1950'S DECADE BOX 9 OZ
SKU: SKU
52155
Products information: More Information                    




More Information


Kosher
No


Brand
NANCY ADAMS


UPC
618645521554


GTIN (case)
10618645521551


Country of Manufacture
United States


Pallet Pattern
12 cases per layer, 7 layers. 84 total cases per pallet.
Sales Per Case: None
Title: 1960'S DECADE BOX 9.25 OZ
SKU: SKU
52156
Products information: More Information                    




More Information


Kosher
No


Brand
NANCY ADAMS


UPC
618645521561


GTIN (case)
10618645521568


Country of Manufacture
United States


Pallet Pattern
12 cases per layer, 7 layers. 84 total cases per pallet.
Sales Per Case: None
Title: 1970'S DECADE BOX 6.5 OZ
SKU: SKU
52157
Products information: More Information                    




More Information


Kosher
No


Brand
NANCY ADAMS


UPC
618645521578


GTIN (case)
10618645521575


Country of Manufacture
United States


Pallet Pattern
12 cases per layer, 7 layers. 84 total cases per pallet.

In [244]:
print(f"Scraped {len(product_list)} records.")

#Convert the list of dictionaries to a DataFrame

df = pd.DataFrame(product_list, columns=['Product Title', 'Product SKU', 'Product Information', 'Sales Per Case'])
df.head(10)

Scraped 5751 records.


Product Title Product SKU  \
0                           1950'S DECADE BOX 9 OZ  SKU\n52155   
1                        1960'S DECADE BOX 9.25 OZ  SKU\n52156   
2                         1970'S DECADE BOX 6.5 OZ  SKU\n52157   
3                         1980'S DECADE BOX 7.6 OZ  SKU\n52158   
4                         1990'S DECADE BOX 7.6 OZ  SKU\n52159   
5                        2000'S DECADE 6.80 OZ BOX  SKU\n52160   
6        CLEVER CANDY - BULK SUGAR STRAWS - PK10LB  SKU\n52584   
7  CLEVER CANDY - COMET CRUSHER - 4IN - JAWBREAKER  SKU\n53035   
8    CLEVER CANDY - GIANT FILLED STRAWS - .42OZ *P  SKU\n51701   
9          CLEVER CANDY - STRAW - 100CT - 6.5OZ *P  SKU\n51959   

                                 Product Information Sales Per Case  
0  More Information                    \n\n\n\n\n...           None  
1  More Information                    \n\n\n\n\n...           None  
2  More Information                    \n\n\n\n\n...           None  
3  More Information                    \n\n\n\n\n...           None  
4  More Information                    \n\n\n\n\n...           None  
5  More Information                    \n\n\n\n\n...           None  
6  More Information                    \n\n\n\n\n...           None  
7  More Information                    \n\n\n\n\n...           None  
8  More Information                    \n\n\n\n\n...           None  
9  More Information                    \n\n\n\n\n...           None

In [245]:
#Iterate over each column
for col in df.columns:
    
    #Convert column values to strings
    df[col] = df[col].astype(str)

    #Split column values at '\n' and expand them into new columns
    split_cols= df[col].str.split('\n', expand= True)

    #Rename the new columns with the original column name + index
    split_cols.columns= [f"{col}_{i}" for i in range(len(split_cols.columns))]

    #Concatenate the new columns to the original DataFrame
    df= pd.concat([df, split_cols], axis=1)

    #Drop the original column
    df.drop(columns=[col], inplace= True)


In [246]:
df.head()

Product Title_0 Product SKU_0 Product SKU_1  \
0     1950'S DECADE BOX 9 OZ           SKU         52155   
1  1960'S DECADE BOX 9.25 OZ           SKU         52156   
2   1970'S DECADE BOX 6.5 OZ           SKU         52157   
3   1980'S DECADE BOX 7.6 OZ           SKU         52158   
4   1990'S DECADE BOX 7.6 OZ           SKU         52159   

                  Product Information_0 Product Information_1  \
0  More Information                                             
1  More Information                                             
2  More Information                                             
3  More Information                                             
4  More Information                                             

  Product Information_2 Product Information_3 Product Information_4  \
0                                                                     
1                                                                     
2                                                                     
3                                                                     
4                                                                     

  Product Information_5 Product Information_6 Product Information_7  \
0      More Information                                               
1      More Information                                               
2      More Information                                               
3      More Information                                               
4      More Information                                               

  Product Information_8 Product Information_9 Product Information_10  \
0                Kosher                    No                          
1                Kosher                    No                          
2                Kosher                    No                          
3                Kosher                    No                          
4                Kosher                    No                          

  Product Information_11 Product Information_12 Product Information_13  \
0                                         Brand            NANCY ADAMS   
1                                         Brand            NANCY ADAMS   
2                                         Brand            NANCY ADAMS   
3                                         Brand            NANCY ADAMS   
4                                         Brand            NANCY ADAMS   

  Product Information_14 Product Information_15 Product Information_16  \
0                                                                  UPC   
1                                                                  UPC   
2                                                                  UPC   
3                                                                  UPC   
4                                                                  UPC   

  Product Information_17 Product Information_18 Product Information_19  \
0           618645521554                                                 
1           618645521561                                                 
2           618645521578                                                 
3           618645521585                                                 
4           618645521592                                                 

  Product Information_20 Product Information_21 Product Information_22  \
0            GTIN (case)         10618645521551                          
1            GTIN (case)         10618645521568                          
2            GTIN (case)         10618645521575                          
3            GTIN (case)         10618645521582                          
4            GTIN (case)         10618645521599                          

  Product Information_23  Product Information_24 Product Information_25  \
0                         Country of Manufacture          United States   
1                         Country of Manufac

In [252]:
# Set display options to show all columns without truncation
pd.set_option('display.max_columns', None)

# Print the DataFrame
df.head()

Product Title_0 Product SKU_0 Product SKU_1  \
0     1950'S DECADE BOX 9 OZ           SKU         52155   
1  1960'S DECADE BOX 9.25 OZ           SKU         52156   
2   1970'S DECADE BOX 6.5 OZ           SKU         52157   
3   1980'S DECADE BOX 7.6 OZ           SKU         52158   
4   1990'S DECADE BOX 7.6 OZ           SKU         52159   

                  Product Information_0 Product Information_1  \
0  More Information                                             
1  More Information                                             
2  More Information                                             
3  More Information                                             
4  More Information                                             

  Product Information_2 Product Information_3 Product Information_4  \
0                                                                     
1                                                                     
2                                                                     
3                                                                     
4                                                                     

  Product Information_5 Product Information_6 Product Information_7  \
0      More Information                                               
1      More Information                                               
2      More Information                                               
3      More Information                                               
4      More Information                                               

  Product Information_8 Product Information_9 Product Information_10  \
0                Kosher                    No                          
1                Kosher                    No                          
2                Kosher                    No                          
3                Kosher                    No                          
4                Kosher                    No                          

  Product Information_11 Product Information_12 Product Information_13  \
0                                         Brand            NANCY ADAMS   
1                                         Brand            NANCY ADAMS   
2                                         Brand            NANCY ADAMS   
3                                         Brand            NANCY ADAMS   
4                                         Brand            NANCY ADAMS   

  Product Information_14 Product Information_15 Product Information_16  \
0                                                                  UPC   
1                                                                  UPC   
2                                                                  UPC   
3                                                                  UPC   
4                                                                  UPC   

  Product Information_17 Product Information_18 Product Information_19  \
0           618645521554                                                 
1           618645521561                                                 
2           618645521578                                                 
3           618645521585                                                 
4           618645521592                                                 

  Product Information_20 Product Information_21 Product Information_22  \
0            GTIN (case)         10618645521551                          
1            GTIN (case)         10618645521568                          
2            GTIN (case)         10618645521575                          
3            GTIN (case)         10618645521582                          
4            GTIN (case)         10618645521599                          

  Product Information_23  Product Information_24 Product Information_25  \
0                         Country of Manufacture          United States   
1                         Country of Manufac

In [248]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5751 entries, 0 to 5750
Data columns (total 50 columns):
 #   Column                  Non-Null Count  Dtype 
---  ------                  --------------  ----- 
 0   Product Title_0         5751 non-null   object
 1   Product SKU_0           5751 non-null   object
 2   Product SKU_1           5751 non-null   object
 3   Product Information_0   5751 non-null   object
 4   Product Information_1   5751 non-null   object
 5   Product Information_2   5751 non-null   object
 6   Product Information_3   5751 non-null   object
 7   Product Information_4   5751 non-null   object
 8   Product Information_5   5751 non-null   object
 9   Product Information_6   5751 non-null   object
 10  Product Information_7   5751 non-null   object
 11  Product Information_8   5751 non-null   object
 12  Product Information_9   5751 non-null   object
 13  Product Information_10  5750 non-null   object
 14  Product Information_11  5750 non-null   object
 15  Prod

In [251]:
#Check the column Product Information_45 the 2 rows is not null
filtered_df = df[df['Product Information_45'].notnull()]

filtered_df

Product Title_0 Product SKU_0  \
891  ASHER'S SUGAR FREE DARK CHOCOLATE FOILED CHERR...           SKU   
906  ASHER'S SUGAR FREE MILK CHOCOLATE FOILED CHERR...           SKU   

    Product SKU_1                 Product Information_0 Product Information_1  \
891         22708  More Information                                             
906         22707  More Information                                             

    Product Information_2 Product Information_3 Product Information_4  \
891                                                                     
906                                                                     

    Product Information_5 Product Information_6 Product Information_7  \
891      More Information                                               
906      More Information                                               

    Product Information_8 Product Information_9 Product Information_10  \
891                Kosher                   Yes                          
906                Kosher                   Yes                          

    Product Information_11 Product Information_12 Product Information_13  \
891                                         Brand                  ASHER   
906                                         Brand                  ASHER   

    Product Information_14 Product Information_15 Product Information_16  \
891                                                             Occasion   
906                                                             Occasion   

    Product Information_17 Product Information_18 Product Information_19  \
891        Valentine's Day                                                 
906        Valentine's Day                                                 

    Product Information_20 Product Information_21 Product Information_22  \
891       Nutrition Claims             Sugar Free                          
906       Nutrition Claims             Sugar Free                          

    Product Information_23 Product Information_24 Product Information_25  \
891                                           UPC           618645227081   
906                                           UPC           618645227074   

    Product Information_26 Product Information_27 Product Information_28  \
891                                                          UPC (inner)   
906                                                          UPC (inner)   

    Product Information_29 Product Information_30 Product Information_31  \
891           089449136464                                                 
906           089449136457                                                 

    Product Information_32 Product Information_33 Product Information_34  \
891         Certifications            Gluten Free                          
906         Certifications            Gluten Free                          

    Product Information_35 Product Information_36 Product Information_37  \
891                                     Pieces/LB                     31   
906                                     Pieces/LB                     31   

    Product Information_38 Product Information_39  Product Information_40  \
891                                                Country of Manufacture   
906                                                Country of Manufacture   

    Product Information_41 Product Information_42 Product Information_43  \
891          United States                                                 
906          United States                                                 

    Product Information_44                             Product Information_45  \
891         Pallet Pattern  8 cases per layer, 4 layers. 32 total cases pe...   
906         Pallet Pattern  8 cases per layer, 4 layers. 32 total cases pe...   

    Sales Per Case_0  
891             None  
906             None

In [258]:
#check the rows isn null for each column start with Product Information_10, 11,12, 13
rows_with_null = df[df['Product Information_10'].isnull()]

rows_with_null #Don't have the rest of information in the site keep as this

Product Title_0 Product SKU_0 Product SKU_1  \
4310  PLASTIC 1 GALLON DISPLAY JARS           SKU         43030   

                     Product Information_0 Product Information_1  \
4310  More Information                                             

     Product Information_2 Product Information_3 Product Information_4  \
4310                                                                     

     Product Information_5 Product Information_6 Product Information_7  \
4310      More Information                                               

     Product Information_8 Product Information_9 Product Information_10  \
4310                Kosher                    No                   None   

     Product Information_11 Product Information_12 Product Information_13  \
4310                   None                   None                   None   

     Product Information_14 Product Information_15 Product Information_16  \
4310                   None                   None                   None   

     Product Information_17 Product Information_18 Product Information_19  \
4310                   None                   None                   None   

     Product Information_20 Product Information_21 Product Information_22  \
4310                   None                   None                   None   

     Product Information_23 Product Information_24 Product Information_25  \
4310                   None                   None                   None   

     Product Information_26 Product Information_27 Product Information_28  \
4310                   None                   None                   None   

     Product Information_29 Product Information_30 Product Information_31  \
4310                   None                   None                   None   

     Product Information_32 Product Information_33 Product Information_34  \
4310                   None                   None                   None   

     Product Information_35 Product Information_36 Product Information_37  \
4310                   None                   None                   None   

     Product Information_38 Product Information_39 Product Information_40  \
4310                   None                   None                   None   

     Product Information_41 Product Information_42 Product Information_43  \
4310                   None                   None                   None   

     Product Information_44 Product Information_45 Sales Per Case_0  
4310                   None                   None             None

In [261]:
#check the rows isn null for each column start with 14
rows_with_null2 = df[df['Product Information_14'].isnull()]

rows_with_null2#same product on the top

Product Title_0 Product SKU_0  \
667                        ALMONDS RAW 32/34 CT 6.25 LB           SKU   
668              ALMONDS ROASTED SALTED 20/22CT 6.25 LB           SKU   
669             ALMONDS ROASTED SALTED 32/34 CT 6.25 LB           SKU   
670            ALMONDS ROASTED UNSALTED 20/22CT 6.25 LB           SKU   
933                                  ASSORTED SPRINKLES           SKU   
1187                     BOBO'S 15 BOX EMPTY FLOOR RACK           SKU   
1256          BUTTER ALMOND ENGLISH TOFFEE *SF DC ONLY*           SKU   
1308           CARAMELETTES MILK CHOCOLATE *SF DC ONLY*           SKU   
1313                    CASHEWS ROASTED UNSALTED 240 CT           SKU   
1389                         CHOCOLATE FLAVORED INSECTS           SKU   
1390                                CHOCOLATE SPRINKLES           SKU   
1391                                CHOCOLATE SPRINKLES           SKU   
1998     FLORALINDA ORANGE BLOSSOM PERFUME *FL DC ONLY*           SKU   
1999  FLORALINDA ORANGE BLOSSOM PERFUME SHELL 0.13 O...           SKU   
2013           FLORIDA ORANGE BOUNCY BALLS *FL DC ONLY*           SKU   
2091  GATOR LEGS ASSORTED ROCK CANDY FLAVORS *FL DC ...           SKU   
2247                    GLACE APRICOTS LARGE 22.046 LBS           SKU   
2570  HITCHERS FLORIDA ASSORTMENT #1 1.5 OZ LOLLIPOP...           SKU   
2571  HITCHERS FLORIDA ASSORTMENT #2 1.5 OZ LOLLIPOP...           SKU   
2572                     HITCHERS ZOO ASSORTMENT 1.5 OZ           SKU   
2615                          HOTLIX ASSORTED WORM POPS           SKU   
2796                     JELLY BELLY CURVE RACK PEG KIT           SKU   
3053            JUSTICE LEAGUE CANDY STICKS WITH TATTOO           SKU   
3303                        LINDT - RACK - 3 TIER - PK1           SKU   
3812               MILK CHOCOLATE HAYSTACKS *SF DC ONY*           SKU   
4310                      PLASTIC 1 GALLON DISPLAY JARS           SKU   
4346               POP UPS MINIONS 1.26 OZ BLISTER PACK           SKU   
4450                                        RAW CASHEWS           SKU   
4451                           RAW FANCY CASHEWS 320 CT           SKU   
4605                      ROASTED SALTED CASHEWS 240 CT           SKU   
4606                      ROASTED SALTED CASHEWS 320 CT           SKU   
4607          ROASTED UNSALTED ALMONDS 32/34 CT 6.25 LB           SKU   
4609                    ROASTED UNSALTED CASHEWS 320 CT           SKU   
4702                     SESAME STICKS CHEDDAR FLAVORED           SKU   
4980  STAINLESS STEEL FRUIT SPOON 2 PC CARDED #2115 ...           SKU   
5353  TORTUGA A TASTE OF FLORIDA COCONUT RUM CAKE 4 ...           SKU   
5355  TORTUGA A TASTE OF FLORIDA ORANGE RUM CAKE 4 O...           SKU   
5520                                VICK'S CHERRY DROPS           SKU   

     Product SKU_1                 Product Information_0  \
667            900  More Information                       
668          24356  More Information                       
669            935  More Information                       
670          24357  More Information                       
933           2032  More Information                       
1187        915299  More Information                       
1256         34132  More Information                       
1308         34172  More Information                       
1313          1685  More Information                       
1389         36037  More Information                       
1390         17867  More Information                       
1391          2031  More Information                       
1998         36754  More Information                       
1999         36753  More Information                       
2013         36732  More Information                       
2091         36860  More Information                       
2247           990  More Information                       
2570         36854  More Information                       
2571         36855  More Information                

In [227]:
columns_to_drop= ['Product SKU_0','Product Information_0','Product Information_1', 'Product Information_2', 'Product Information_3', 'Product Information_4',
                   'Product Information_5','Product Information_6', 'Product Information_7','Product Information_8', 'Product Information_9',
                    'Product Information_10', 'Product Information_11','Product Information_12', 'Product Information_13', 'Product Information_14',
                    'Product Information_15', 'Product Information_16', 'Product Information_18','Product Information_19', 'Product Information_20',
                    'Product Information_22', 'Product Information_23', 'Product Information_24', 'Product Information_25','Product Information_26', 
                    'Product Information_27', 'Product Information_28', 'Product Information_30','Product Information_31', 'Product Information_32',
                    'Product Information_33', 'Product Information_34', 'Product Information_35', 'Product Information_36', 'Product Information_37',
                    'Product Information_38','Product Information_39', 'Product Information_40', 'Product Information_41', 'Product Information_42', 
                    'Product Information_43', 'Product Information_44','Product Information_45']

df.drop(columns=columns_to_drop, inplace=True)

df.head()

Product Title_0 Product SKU_1 Product Information_17  \
0     1950'S DECADE BOX 9 OZ         52155           618645521554   
1  1960'S DECADE BOX 9.25 OZ         52156           618645521561   
2   1970'S DECADE BOX 6.5 OZ         52157           618645521578   
3   1980'S DECADE BOX 7.6 OZ         52158           618645521585   
4   1990'S DECADE BOX 7.6 OZ         52159           618645521592   

  Product Information_21                             Product Information_29  \
0         10618645521551  12 cases per layer, 7 layers. 84 total cases p...   
1         10618645521568  12 cases per layer, 7 layers. 84 total cases p...   
2         10618645521575  12 cases per layer, 7 layers. 84 total cases p...   
3         10618645521582  12 cases per layer, 7 layers. 84 total cases p...   
4         10618645521599  12 cases per layer, 7 layers. 84 total cases p...   

  Sales Per Case_0  
0             None  
1             None  
2             None  
3             None  
4             None

In [228]:
#Getting necessary columns
new_df= df[['Product Title_0', 'Product SKU_1', 'Product Information_17', 'Product Information_21', 'Product Information_29', 'Sales Per Case_0']]

#Rename the columns
new_column_names = {
    'Product Title_0': 'Product_Title',
    'Product SKU_1': 'SKU',
    'Product Information_17': 'UPC',
    'Product Information_21': 'GTIN',
    'Product Information_29': 'Pallet',
    'Sales Per Case_0':'Sales_Per_Case'
}

new_df.rename(columns=new_column_names, inplace=True)


new_df.head()

Product_Title    SKU           UPC            GTIN  \
0     1950'S DECADE BOX 9 OZ  52155  618645521554  10618645521551   
1  1960'S DECADE BOX 9.25 OZ  52156  618645521561  10618645521568   
2   1970'S DECADE BOX 6.5 OZ  52157  618645521578  10618645521575   
3   1980'S DECADE BOX 7.6 OZ  52158  618645521585  10618645521582   
4   1990'S DECADE BOX 7.6 OZ  52159  618645521592  10618645521599   

                                              Pallet Sales_Per_Case  
0  12 cases per layer, 7 layers. 84 total cases p...           None  
1  12 cases per layer, 7 layers. 84 total cases p...           None  
2  12 cases per layer, 7 layers. 84 total cases p...           None  
3  12 cases per layer, 7 layers. 84 total cases p...           None  
4  12 cases per layer, 7 layers. 84 total cases p...           None

In [229]:

# Check for duplicates based on the specified columns
duplicates = new_df[new_df.duplicated(subset=['SKU','UPC', 'GTIN'], keep=False)]

# Print the duplicates
print("Duplicate rows based on the specified columns:")
duplicates.head()

Duplicate rows based on the specified columns:


Empty DataFrame
Columns: [Product_Title, SKU, UPC, GTIN, Pallet, Sales_Per_Case]
Index: []

In [230]:
# Drop duplicates based on the UPC column
new_df.drop_duplicates(duplicates)

# Print the DataFrame after dropping duplicates
new_df.head()

Product_Title    SKU           UPC            GTIN  \
0     1950'S DECADE BOX 9 OZ  52155  618645521554  10618645521551   
1  1960'S DECADE BOX 9.25 OZ  52156  618645521561  10618645521568   
2   1970'S DECADE BOX 6.5 OZ  52157  618645521578  10618645521575   
3   1980'S DECADE BOX 7.6 OZ  52158  618645521585  10618645521582   
4   1990'S DECADE BOX 7.6 OZ  52159  618645521592  10618645521599   

                                              Pallet Sales_Per_Case  
0  12 cases per layer, 7 layers. 84 total cases p...           None  
1  12 cases per layer, 7 layers. 84 total cases p...           None  
2  12 cases per layer, 7 layers. 84 total cases p...           None  
3  12 cases per layer, 7 layers. 84 total cases p...           None  
4  12 cases per layer, 7 layers. 84 total cases p...           None

In [231]:
new_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5751 entries, 0 to 5750
Data columns (total 6 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   Product_Title   5751 non-null   object
 1   SKU             5751 non-null   object
 2   UPC             5713 non-null   object
 3   GTIN            5485 non-null   object
 4   Pallet          4314 non-null   object
 5   Sales_Per_Case  5751 non-null   object
dtypes: object(6)
memory usage: 269.7+ KB


In [243]:
rows_with_null = new_df[new_df.isnull().any(axis=1)]
rows_with_null.info()

<class 'pandas.core.frame.DataFrame'>
Index: 1437 entries, 11 to 5750
Data columns (total 6 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   Product_Title   1437 non-null   object
 1   SKU             1437 non-null   object
 2   UPC             1399 non-null   object
 3   GTIN            1171 non-null   object
 4   Pallet          0 non-null      object
 5   Sales_Per_Case  1437 non-null   object
dtypes: object(6)
memory usage: 78.6+ KB


In [22]:
# Write DataFrame to a CSV file
final_dataFrame.to_excel('Resources/apparel.xlsx', index=False)

In [24]:
def get_summary():
    baby_list = []
    page_num = 1
    visited_UPCs = set()  # Set to keep track of visited UPCs

    while True:
        # Visit the URL for the current page
        browser.visit(f"https://www.updinc.net/catalog/?catid=10&pageNum={page_num}")
        
        # Get the HTML content
        html = browser.html
        soup = BeautifulSoup(html, 'html.parser')
        
        # Find the product boxes
        found_babies = soup.find_all('div', class_='prdct-box')

        if not found_babies:
            break

        for baby in found_babies:
            name = baby.find("div", class_="prdct-box2").text.strip()
            UPC = baby.find('div', class_='prdct-box3').text.strip()

            # Check if UPC has been visited before
            if UPC not in visited_UPCs:
                summary_dict = {'name': name, 'UPC': UPC}
                baby_list.append(summary_dict)
                visited_UPCs.add(UPC)  # Add UPC to visited set
            
        # Move to the next page
        page_num += 1
    
    return baby_list

In [25]:
babies_list=[]
for _ in range(1):
    summary=get_summary()
    babies_list.extend(get_summary())
    
babies_list

[{'name': 'Wholesale Little Tikes Fish & Chips Action Game\nItem: 13422\n$5.45 EachSelect Quantity:\n\n\n\xa04\xa0\n\xa016\xa0\n\xa028\xa0\n\n\n\xa08\xa0\n\xa020\xa0\n\xa032\xa0\n\n\n\xa012\n\xa024\n\xa036\n\n\nor Enter Quantity:',
  'UPC': 'PRODUCT DETAILS\nItem Size: 8" x 5" x 10.5"\nCase: 4\nInner: \nInner Size: \nUPC: 686141134226\nWT: 4\nCF: 1.19\nSub-Category: BB02\nOrigin: China'},
 {'name': 'Wholesale Little Tikes Milk & Cookies Action Game\nItem: 13424\n$5.45 EachSelect Quantity:\n\n\n\xa04\xa0\n\xa016\xa0\n\xa028\xa0\n\n\n\xa08\xa0\n\xa020\xa0\n\xa032\xa0\n\n\n\xa012\n\xa024\n\xa036\n\n\nor Enter Quantity:',
  'UPC': 'PRODUCT DETAILS\nItem Size: 8" x 5" x 10.5"\nCase: 4\nInner: \nInner Size: \nUPC: 686141134240\nWT: 5\nCF: 1.29\nSub-Category: BB02\nOrigin: China'},
 {'name': 'Wholesale Itsy Tots Baby Activity Walker with sound in color box\nItem: 182209\n$14.25 EachSelect Quantity:\n\n\n\xa06\xa0\n\xa024\xa0\n\xa042\xa0\n\n\n\xa012\xa0\n\xa030\xa0\n\xa048\xa0\n\n\n\xa018\n\xa

In [26]:
print(f"Scraped {len(babies_list)} records.")
baby_list_df= pd.DataFrame(babies_list)
baby_list_df.head()

Scraped 54 records.


name  \
0  Wholesale Little Tikes Fish & Chips Action Gam...   
1  Wholesale Little Tikes Milk & Cookies Action G...   
2  Wholesale Itsy Tots Baby Activity Walker with ...   
3  Wholesale Itsy Tots Junior Mechanic Plane in w...   
4  Wholesale Safety 1st 2 Pk Glow In The Dark Pac...   

                                                 UPC  
0  PRODUCT DETAILS\nItem Size: 8" x 5" x 10.5"\nC...  
1  PRODUCT DETAILS\nItem Size: 8" x 5" x 10.5"\nC...  
2  PRODUCT DETAILS\nItem Size: 18" x 4.25" x 13.2...  
3  PRODUCT DETAILS\nItem Size: 7" x 5.5" x 5.5"\n...  
4  PRODUCT DETAILS\nItem Size: 4" x 2" x 4.5"\nCa...

In [28]:
# Concatenate 'name' and 'UPC' columns with a separator
baby_list_df['concatenated'] = baby_list_df['name'] + '\n' + baby_list_df['UPC']

# Calculate the maximum number of elements in any row after splitting
max_len = max(len(row.split('\n')) for row in baby_list_df['concatenated'])

# Split the data into separate columns and pad shorter rows with None values
data_list2 = [row.split('\n') + [None] * (max_len - len(row.split('\n'))) for row in baby_list_df['concatenated'] if row.strip()]

# Create a DataFrame from the split data
baby_list_data = pd.DataFrame(data_list2)

# Rename the columns
baby_list_data.columns = [f'Column_{i+1}' for i in range(max_len)]

# Print the new DataFrame
baby_list_data.head()

Column_1      Column_2  \
0    Wholesale Little Tikes Fish & Chips Action Game   Item: 13422   
1  Wholesale Little Tikes Milk & Cookies Action Game   Item: 13424   
2  Wholesale Itsy Tots Baby Activity Walker with ...  Item: 182209   
3  Wholesale Itsy Tots Junior Mechanic Plane in w...    Item: 2010   
4  Wholesale Safety 1st 2 Pk Glow In The Dark Pac...   Item: 20973   

                      Column_3 Column_4 Column_5 Column_6 Column_7 Column_8  \
0   $5.45 EachSelect Quantity:                         4       16       28    
1   $5.45 EachSelect Quantity:                         4       16       28    
2  $14.25 EachSelect Quantity:                         6       24       42    
3   $3.91 EachSelect Quantity:                        12       48       84    
4   $1.27 EachSelect Quantity:                        36      144      252    

  Column_9 Column_10  ...        Column_22                       Column_23  \
0                     ...  PRODUCT DETAILS      Item Size: 8" x 5" x 10.5"   
1                     ...  PRODUCT DETAILS      Item Size: 8" x 5" x 10.5"   
2                     ...  PRODUCT DETAILS  Item Size: 18" x 4.25" x 13.2"   
3                     ...  PRODUCT DETAILS     Item Size: 7" x 5.5" x 5.5"   
4                     ...  PRODUCT DETAILS       Item Size: 4" x 2" x 4.5"   

  Column_24 Column_25     Column_26          Column_27 Column_28 Column_29  \
0   Case: 4   Inner:   Inner Size:   UPC: 686141134226     WT: 4  CF: 1.19   
1   Case: 4   Inner:   Inner Size:   UPC: 686141134240     WT: 5  CF: 1.29   
2   Case: 6   Inner:   Inner Size:   UPC: 810076720470    WT: 21  CF: 4.16   
3  Case: 12   Inner:   Inner Size:   UPC: 678634883056     WT: 9  CF: 1.77   
4  Case: 36   Inner:   Inner Size:   UPC: 810002209734     WT: 5  CF: 0.68   

            Column_30      Column_31  
0  Sub-Category: BB02  Origin: China  
1  Sub-Category: BB02  Origin: China  
2  Sub-Category: BB02  Origin: China  
3  Sub-Category: BB02  Origin: China  
4  Sub-Category: BB01  Origin: China  

[5 rows x 31 columns]

In [29]:
#Getting necessary columns
new_baby_list_df= baby_list_data[['Column_1', 'Column_2', 'Column_3', 'Column_24', 'Column_27']]

#Rename the columns
new_column_names = {
    'Column_1': 'Item_Name',
    'Column_2': 'Item_Number',
    'Column_3': 'Price',
    'Column_24': 'Quantity',
    'Column_27': 'UPC'
}

new_baby_list_df.rename(columns=new_column_names, inplace=True)

# Remove 'Wholesale' from the column 'Item_Name'
new_baby_list_df['Item_Name'] = new_baby_list_df['Item_Name'].str.replace('Wholesale', '')

#Remove 'Item:' from the column 'Item_Number'
new_baby_list_df['Item_Number'] = new_baby_list_df['Item_Number'].str.replace('Item:', '')

#Remove 'EachSelect Quantity:' from the column 'Price'
new_baby_list_df['Price'] = new_baby_list_df['Price'].str.replace('EachSelect Quantity:', '')

#Remove 'UPC' from the column 'UPC'
new_baby_list_df['UPC'] = new_baby_list_df['UPC'].str.replace('UPC:', '')

#Remove 'UPC' from the column 'UPC'
new_baby_list_df['Quantity'] = new_baby_list_df['Quantity'].str.replace('Case:', '')

new_baby_list_df.head()

C:\Users\Fernanda\AppData\Local\Temp\ipykernel_11576\1844083878.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_baby_list_df.rename(columns=new_column_names, inplace=True)
C:\Users\Fernanda\AppData\Local\Temp\ipykernel_11576\1844083878.py:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_baby_list_df['Item_Name'] = new_baby_list_df['Item_Name'].str.replace('Wholesale', '')
C:\Users\Fernanda\AppData\Local\Temp\ipykernel_11576\1844083878.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[ro

Item_Name Item_Number    Price  \
0              Little Tikes Fish & Chips Action Game       13422   $5.45    
1            Little Tikes Milk & Cookies Action Game       13424   $5.45    
2   Itsy Tots Baby Activity Walker with sound in ...      182209  $14.25    
3      Itsy Tots Junior Mechanic Plane in window box        2010   $3.91    
4   Safety 1st 2 Pk Glow In The Dark Pacifier W/ ...       20973   $1.27    

  Quantity            UPC  
0        4   686141134226  
1        4   686141134240  
2        6   810076720470  
3       12   678634883056  
4       36   810002209734

In [30]:
# Check for duplicates based on the specified columns
duplicates2 = new_baby_list_df[new_baby_list_df.duplicated(subset=['Item_Name','Item_Number', 'Price', 'UPC'], keep=False)]

# Print the duplicates
print("Duplicate rows based on the specified columns:")
duplicates2.head()

Duplicate rows based on the specified columns:


Empty DataFrame
Columns: [Item_Name, Item_Number, Price, Quantity, UPC]
Index: []

In [31]:
# Drop duplicates based on the UPC column
new_baby_list_df.drop_duplicates(duplicates2)

# Print the DataFrame after dropping duplicates
new_baby_list_df.head()

Item_Name Item_Number    Price  \
0              Little Tikes Fish & Chips Action Game       13422   $5.45    
1            Little Tikes Milk & Cookies Action Game       13424   $5.45    
2   Itsy Tots Baby Activity Walker with sound in ...      182209  $14.25    
3      Itsy Tots Junior Mechanic Plane in window box        2010   $3.91    
4   Safety 1st 2 Pk Glow In The Dark Pacifier W/ ...       20973   $1.27    

  Quantity            UPC  
0        4   686141134226  
1        4   686141134240  
2        6   810076720470  
3       12   678634883056  
4       36   810002209734

In [32]:
new_baby_list_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 54 entries, 0 to 53
Data columns (total 5 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   Item_Name    54 non-null     object
 1   Item_Number  54 non-null     object
 2   Price        54 non-null     object
 3   Quantity     54 non-null     object
 4   UPC          54 non-null     object
dtypes: object(5)
memory usage: 2.2+ KB


In [33]:
#Changing the column oreder
# Define the new sequence of column names
new_column_order = ['Item_Number','Item_Name', 'Price', 'Quantity', 'UPC' ]

# Reorder the columns based on the new sequence
final_dataFrame2 = new_baby_list_df[new_column_order]
final_dataFrame2.head()

Item_Number                                          Item_Name    Price  \
0       13422              Little Tikes Fish & Chips Action Game   $5.45    
1       13424            Little Tikes Milk & Cookies Action Game   $5.45    
2      182209   Itsy Tots Baby Activity Walker with sound in ...  $14.25    
3        2010      Itsy Tots Junior Mechanic Plane in window box   $3.91    
4       20973   Safety 1st 2 Pk Glow In The Dark Pacifier W/ ...   $1.27    

  Quantity            UPC  
0        4   686141134226  
1        4   686141134240  
2        6   810076720470  
3       12   678634883056  
4       36   810002209734

In [34]:
# Write DataFrame to a CSV file
final_dataFrame2.to_excel('Resources/baby.xlsx', index=False)